# Setting up

In [6]:
import json
import random
import os, sys
from IPython.display import display, clear_output, HTML
from random import randrange, choice
import matplotlib.pyplot as plt
plt.rcParams["figure.figsize"]=25,25
import numpy as np
import seaborn as sns
import re

random.seed(42)
!git clone http://gitlab.aicrowd.com/amazon-prime-air/airborne-detection-starter-kit.git
os.chdir("airborne-detection-starter-kit/data")

Cloning into 'airborne-detection-starter-kit'...
remote: Enumerating objects: 23, done.
remote: Counting objects: 100% (23/23), done.
remote: Compressing objects: 100% (20/20), done.
remote: Total 360 (delta 9), reused 8 (delta 3), pack-reused 337
Receiving objects: 100% (360/360), 21.91 MiB | 11.94 MiB/s, done.
Resolving deltas: 100% (148/148), done.


In [8]:
# Dataset for Airborne Object Tracking Dataset
sys.path.append(os.path.dirname(os.path.realpath(os.getcwd())))
sys.path.append(os.path.dirname(os.path.realpath(os.getcwd())) + "/core")
!pip install -r ../requirements.txt > /dev/null
from core.dataset import Dataset
notebook_path = os.path.dirname(os.path.realpath("__file__"))

local_path = notebook_path + '/part1'
s3_path = 's3://airborne-obj-detection-challenge-training/part1/'
dataset = Dataset(local_path, s3_path, prefix='part1')

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
datascience 0.10.6 requires folium==0.2.1, but you have folium 0.8.3 which is incompatible.


2021-09-11 10:34:32.337 | INFO     | core.dataset:load_gt:20 - Loading ground truth...
2021-09-11 10:34:32.344 | INFO     | core.file_handler:download_file_if_needed:33 - [download_from_s3] File not found locally, downloading: ImageSets/groundtruth.json


In [9]:
# `local_path` -> dataset is automatically downloaded to that folder
# `s3_path` -> location to look for images in case they aren't present locally

# You can add multi-part dataset as well, using below..
local_path = notebook_path + '/part2'
s3_path = 's3://airborne-obj-detection-challenge-training/part2/'
dataset.add(local_path, s3_path, prefix='part2')

# You can add multi-part dataset as well, using below..
local_path = notebook_path + '/part3'
s3_path = 's3://airborne-obj-detection-challenge-training/part3/'
dataset.add(local_path, s3_path, prefix='part3')

2021-09-11 10:39:19.157 | INFO     | core.dataset:load_gt:20 - Loading ground truth...
2021-09-11 10:39:19.161 | INFO     | core.file_handler:download_file_if_needed:33 - [download_from_s3] File not found locally, downloading: ImageSets/groundtruth.json
2021-09-11 10:39:54.739 | INFO     | core.dataset:load_gt:20 - Loading ground truth...
2021-09-11 10:39:54.743 | INFO     | core.file_handler:download_file_if_needed:33 - [download_from_s3] File not found locally, downloading: ImageSets/groundtruth.json


# Creating txt file for each flight


In [10]:
import cv2
from google.colab.patches import cv2_imshow
import xml.etree.ElementTree as gfg 

In [11]:
all_flight_ids = dataset.get_flight_ids()
print("We have {0} total number of flights".format(len(all_flight_ids)))

flight = dataset.get_flight_by_id(all_flight_ids[100])
print("Example on a flight", flight)

We have 4154 total number of flights
Example on a flight Flight#part131231837a3484249938d052a58fd59e3(num_frames=1199, num_airborne_objs=3)


In [12]:
import json 
flights_ids_remove = []
flights_ids = []
final_flights = 0
for id in all_flight_ids:
  flight = dataset.get_flight_by_id(id)
  if len(flight.detected_objects) == 0:
    flights_ids_remove.append(id)
    continue
  final_flights += 1  
  flights_ids.append(id)
print(len(flights_ids_remove))
print(final_flights)

268
3886


In [ ]:
image_area =  (2448/4)*(2048/4)

file1 = open("dataset_new.txt", "a") 
for id in flights_ids:
  print(id)
  test_flight = dataset.get_flight_by_id(id)
  final_flight_keys = []
  flight_keys = test_flight.frames.keys()
  airborne_objects = test_flight.detected_objects
  final_flight_keys = []
  for key in flight_keys:
    test_frame = test_flight.get_frame(key)
    if test_frame.num_detected_objects == 0:
      continue
    bbs = []
    frame_objects = []
    final_flight_keys.append(key)
    for obj in airborne_objects:
      
      if obj in test_frame.detected_object_locations:
        frame_objects.append(obj)
        bb = test_frame.detected_object_locations[obj].bb
        bbs.append(bb)

    #  writing XML file for each frame
    img_path = test_frame.image_path()
    path = "/content/airborne-detection-starter-kit/data/part1/"
    img_name = (os.path.splitext(test_frame.image_path())[0]).rsplit('/', 1)[-1]
    path = '/content/airborne-detection-starter-kit/data/images_xml'

  # To implement a foor loop, itterates over all objects and append them to the XML file
    count = 0
    for obj in frame_objects:
      w = (bbs[count].width)//4
      h = (bbs[count].height)//4
      area_obj = w*h 
      count +=1
      str_key = str(key)
      obje = re.sub("\d", "", obj)
      # print(obje)
      file1.write(test_flight.id + "," + str_key + "," + path + img_path + "," +  str(((area_obj/image_area)*100)) +","+ obje + "," + str(2448/4) + ","+ str(2048/4) +"\n")

part163c5597a57b04b448723f1f1844a2b78
part100bb96a5a68f4fa5bc5c5dc66ce314d2
part182c003b45857406b8eded5115cc0118d
part1829d263844ed4387b374fe9db9a510e4
part14458bb328345402c8f363b7480060393
part143a99be53c3a4176a8f7d9e10f8bd29c
part14d196dd04a23411193d525b2356a1187
part101a7a84b9226468bbb7f88d483c3e996
part16e8de53f981f481c8090c7bcb9f66b44
part10f7714af364842449ee42f31b0446e2f
part140a522741b434597869ea7d751ad6c7d
part17f5dd587c1b046efbf9e3221fe633e4e
part12a3f9954e29a494c822d1a28adf5cd51
part13c349bdf14c1464bb2b30094e7297d84
part169904ae4f18d46ec8886e8fd6179171b
part11b276556ba4444baaae96589623ba18c
part104e4d5704d1e4a18933a544c86826064
part1631e499cdbd64dbeafec76d54e0f2716
part114c25ef422b64c3b8114d92cf5de4cfb
part13fd5b63cb26844bba1eb9a712db38973
part16d2916d00dd940f4b67d31856b2af7a1
part13d739c8d23d240f68fd84aeda4577fa5
part11748d11a89fd4ded8885a3778b1241b5
part107243f3c7ff24aa0819c8857f0c8d07e
part15f95596edc86439dbd19a252ff5760b7
part119a401572b9d4a7fa044ba10b616886b
part11d13f49

copy the file path into the drive and read it later to transfer data to s3 bucket

# Reading image data from a text file 

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [13]:
import pandas as pd
colnames=["flight_id", "frame_key", 'path', 'ratio', 'object', 'img_width', 'img_height'] 
df = pd.read_csv('/content/drive/MyDrive/MLC_data/data/dataset_new.txt', delimiter = ",",names=colnames )

In [43]:
df.head()

flight_id  frame_key  ... img_width  img_height
0  part163c5597a57b04b448723f1f1844a2b78          2  ...     612.0       512.0
1  part163c5597a57b04b448723f1f1844a2b78          3  ...     612.0       512.0
2  part163c5597a57b04b448723f1f1844a2b78          4  ...     612.0       512.0
3  part163c5597a57b04b448723f1f1844a2b78          5  ...     612.0       512.0
4  part163c5597a57b04b448723f1f1844a2b78          6  ...     612.0       512.0

[5 rows x 7 columns]

In [ ]:
df.shape

(2891875, 7)

In [15]:
df2 = df[df['ratio'] > 0.5]

In [44]:
df2.head()

flight_id  frame_key  ... img_width  img_height
5763  part101a7a84b9226468bbb7f88d483c3e996        841  ...     612.0       512.0
6758  part10f7714af364842449ee42f31b0446e2f        861  ...     612.0       512.0
6759  part10f7714af364842449ee42f31b0446e2f        862  ...     612.0       512.0
6760  part10f7714af364842449ee42f31b0446e2f        863  ...     612.0       512.0
6761  part10f7714af364842449ee42f31b0446e2f        864  ...     612.0       512.0

[5 rows x 7 columns]

In [45]:
df2.shape

(9941, 7)

In [ ]:
df['flight_id'].unique()

array(['part163c5597a57b04b448723f1f1844a2b78 ',
       'part100bb96a5a68f4fa5bc5c5dc66ce314d2 ',
       'part182c003b45857406b8eded5115cc0118d ', ...,
       'part1844068b7a0914bcd98f431c9d2fb1519 ',
       'part149d0653e64804c4bab8b781aadd49dce ',
       'part146373155e5994db681f6b88f7813adc5 '], dtype=object)

**Uploading Data into S3 bucket**

In [ ]:
#installing boto3 for connecting to s3
!pip install boto3

In [ ]:
AWS_KEY_ID = '*******'
AWS_SECRET_KEY = '**********'
BUCKET_NAME = 'airborne-object-detection'

In [18]:
import boto3
#Creating Session With Boto3.
session = boto3.Session(
aws_access_key_id=AWS_KEY_ID,
aws_secret_access_key=AWS_SECRET_KEY
)


In [19]:
s3_bucket = session.resource('s3')

In [41]:
for index, row in df2.iterrows(): 
  flight = dataset.get_flight_by_id(row['flight_id'].strip())
  airborne_objects = flight.detected_objects
  frame = flight.get_frame(row['frame_key'])
  # print(flight, "\n", airborne_objects, "\n", frame)

  img = frame.image()
  # To change img to 1 channel, resize and save it to s3 to folder Dataset_v1 then delete it from colab
  
  dist_part = flight.id[0:5]
  path_to_remove = "/content/airborne-detection-starter-kit/data/" + dist_part +"/"+ frame.image_path()
  
  image = cv2.imread(path_to_remove, cv2.IMREAD_GRAYSCALE)
  print(image.shape)
  height = image.shape[0]
  width = image.shape[1]

  dst = cv2.resize(image, (int(width/4), int(height/4)))

  print(dst.shape)
  img_name = (os.path.splitext(frame.image_path())[0]).rsplit('/', 1)[-1]
  path = '/content/xmls/'
  cv2.imwrite(os.path.join(path , img_name+ ".png"), dst)
  # object = s3_bucket.Object('airborne-object-detection', 'dataset_v1_ratio_0.5/'+path + "" +img_name+ ".png")
  # result = object.put(Body=dst)
  # s3_bucket.meta.client.upload_file(os.path.join(path , img_name+ ".png"), 'airborne-object-detection', 'dataset_v2_ratio_0.5'+path + "" +img_name+ ".png")
  os.remove(os.path.join(path , img_name+ ".png"))
  
  bbs = []
  frame_objects = []
  for obj in airborne_objects:  
    if obj in frame.detected_object_locations:
      frame_objects.append(obj)
      bb = frame.detected_object_locations[obj].bb
      bbs.append(bb)
  # print(bbs, frame_objects)
  os.remove(path_to_remove)

  print("-------------------------------------------")
#   #  writing XML file for each frame
  img_path = frame.image_path()
# img_name = os.path.splitext(test_frame.image_path())[0]
  img_name = (os.path.splitext(frame.image_path())[0]).rsplit('/', 1)[-1] 
  root = gfg.Element("annotation")

  s1= gfg.SubElement(root, "folder")
  s1.text = "trainfolder"  

  s2= gfg.SubElement(root, "filename")
  s2.text = os.path.basename(frame.image_path())

  s3= gfg.SubElement(root, "path")
  s3.text = img_path 

  e2 = gfg.Element("source")
  root.append (e2)
  s1_2 = gfg.SubElement(e2, "database")
  s1_2.text = "unknown"

  e3 = gfg.Element("size")
  root.append (e3)
  s1_3 = gfg.SubElement(e3, "width")
  s1_3.text = str(row['img_width'])
  s2_3 = gfg.SubElement(e3, "height")
  s2_3.text = str(row['img_height'])
  s3_3 = gfg.SubElement(e3, "depth")
  s3_3.text = str(1)

  s4= gfg.SubElement(root, "segmented")
  s4.text = "0"  

# # To implement a foor loop, itterates over all objects and append them to the XML file 
  count = 0
  for obj in frame_objects:
    e4 = gfg.Element("object")
    root.append (e4)
    s1_4 = gfg.SubElement(e4, "name")
    s1_4.text = re.sub("\d", "", obj)
    s2_4 = gfg.SubElement(e4, "pose")
    s2_4.text = "unspecified"
    s3_4 = gfg.SubElement(e4, "difficult")
    s3_4.text = "0"
    s4_4 = gfg.SubElement(e4, "bndbox")
    s1_4_4 = gfg.SubElement(s4_4, "xmin")
    s1_4_4.text = str((bbs[count].left)//4)
    s2_4_4 = gfg.SubElement(s4_4, "ymin")
    s2_4_4.text = str((bbs[count].top)//4)
    s3_4_4 = gfg.SubElement(s4_4, "xmax")
    s3_4_4.text = str((bbs[count].left + bbs[count].width)//4)
    s4_4_4 = gfg.SubElement(s4_4, "ymax")
    s4_4_4.text = str((bbs[count].top + bbs[count].height)//4)
    count +=1
  
    tree = gfg.ElementTree(root)
    xml_path =   "/content/xmls/"+img_name + ".xml"
    with open (xml_path, "wb") as files :
        tree.write(files)   
    # To save this xml file to s3 to folder Dataset_v1 then delete it from colab
    s3_bucket.meta.client.upload_file(xml_path, 'airborne-object-detection', 'dataset_v2_ratio_0.5'+xml_path)
    os.remove(xml_path)



2021-09-11 17:07:47.931 | INFO     | core.file_handler:download_file_if_needed:33 - [download_from_s3] File not found locally, downloading: Images/01a7a84b9226468bbb7f88d483c3e996/156759467143662089801a7a84b9226468bbb7f88d483c3e996.png


(2048, 2448)
(512, 612)
-------------------------------------------


2021-09-11 17:07:48.959 | INFO     | core.file_handler:download_file_if_needed:33 - [download_from_s3] File not found locally, downloading: Images/0f7714af364842449ee42f31b0446e2f/15507424931263551660f7714af364842449ee42f31b0446e2f.png
2021-09-11 17:07:49.716 | INFO     | core.file_handler:download_file_if_needed:33 - [download_from_s3] File not found locally, downloading: Images/0f7714af364842449ee42f31b0446e2f/15507424932262367370f7714af364842449ee42f31b0446e2f.png


(2048, 2448)
(512, 612)
-------------------------------------------


2021-09-11 17:07:50.462 | INFO     | core.file_handler:download_file_if_needed:33 - [download_from_s3] File not found locally, downloading: Images/0f7714af364842449ee42f31b0446e2f/15507424933538937640f7714af364842449ee42f31b0446e2f.png


...

(2048, 2448)
(512, 612)
-------------------------------------------


2021-09-11 19:53:16.557 | INFO     | core.file_handler:download_file_if_needed:33 - [download_from_s3] File not found locally, downloading: Images/d329e256bdde474b84cd9ae18085dfc4/1560781459059369276d329e256bdde474b84cd9ae18085dfc4.png


(2048, 2448)
(512, 612)
-------------------------------------------


2021-09-11 19:53:17.475 | INFO     | core.file_handler:download_file_if_needed:33 - [download_from_s3] File not found locally, downloading: Images/9542c0ca09d84a80983865bd4e86bbfe/15520377896054064619542c0ca09d84a80983865bd4e86bbfe.png


(2048, 2448)
(512, 612)
-------------------------------------------
